In [1]:
import pickle
import string

from babel.dates import format_date

import altair as alt
import numpy as np
import pandas as pd
import re
import spacy

from bs4 import BeautifulSoup
from french_lefff_lemmatizer.french_lefff_lemmatizer import FrenchLefffLemmatizer
from gensim.corpora.dictionary import Dictionary

from utils.data import notes, resultats

In [2]:
pd.options.display.max_colwidth = 200
DEFAULT_WIDTH = 800

_ = alt.data_transformers.disable_max_rows()

In [3]:
with open("canebiere.pickle", "rb") as src:
    df: pd.DataFrame = pickle.load(src)



___


# Blaah l'académicien


In [4]:
blaah = df[df['Auteur'] == 'Blaah'].reset_index()

In [5]:
last = blaah.loc[blaah['Date'].argmax()]
print(f"Dernière Académie: {format_date(last['Date'], locale='fr_FR')} / {last['Titre']}")

Dernière Académie: 15 mai 2022 / Rennes-OM (2-0), La Canebière académie est insupportable


## Mots les plus utilisés

In [6]:
lemmatizer = FrenchLefffLemmatizer()

def lemmatize(x: spacy.tokens.Token) -> str:
    pos_2_leff = {
        "VERB": "v",
        "NOUN": "n",
        "ADJ": "a"
    }
    leff_pos = pos_2_leff.get(x.pos_, "n")
    return lemmatizer.lemmatize(word=x.lemma_, pos=leff_pos)

corpus = [[lemmatize(t) for t in doc if not t.is_stop and not t.is_space and len(t) > 2] for doc in blaah["docs"]]
dic = Dictionary(documents=corpus)

## Mots utilisés dans le plus d'académies

In [7]:
dfs = pd.DataFrame([{"word": dic[k], "dfs": v} for k, v in dic.dfs.items()])
dfs['first_letter'] = dfs['word'].str[0].str.upper()

dropdown_letter = alt.binding_select(options=list(string.ascii_uppercase), name="Première lettre: ")
select_first_letter = alt.selection_single(name="firstletter", fields=["first_letter"], bind=dropdown_letter, init={"first_letter": 'A'})

slider_docfreq = alt.binding_range(min=dfs['dfs'].min(), max=dfs['dfs'].max(), step=1, name="Nombre Minimum d'Académies: ")
select_nb_acad = alt.selection_single(name="nbacads", fields=["dfs"], bind=slider_docfreq, init={"dfs": 20})

alt.Chart(dfs.sort_values('word')).mark_bar().encode(
    y=alt.Y(
        "dfs:Q", 
        title="Nombre d'académies utilisant le mot",
        scale=alt.Scale(domain=[0, dfs['dfs'].max()])
    ),
    x=alt.X(
        "word:O", 
        axis=alt.Axis(labelAngle=-45),
        title="Mot"
    ),
    color=alt.Color("dfs", scale=alt.Scale(scheme="redyellowgreen", domain=[0, dfs['dfs'].max()])),
    tooltip=[alt.Tooltip(field="word", title="Mot"), alt.Tooltip(field="dfs", title="# Académies")]
).add_selection(
    select_first_letter,
    select_nb_acad
).transform_filter(
    select_first_letter
).transform_filter(
    "datum.dfs >= nbacads_dfs"
).properties(
    height=400
)

alt.Chart(...)

## Mots les plus fréquents

In [8]:
cfs = pd.DataFrame([{"word": dic[k], "cfs": v} for k, v in dic.cfs.items()])
cfs['first_letter'] = cfs['word'].str[0].str.upper()

dropdown_letter = alt.binding_select(options=list(string.ascii_uppercase), name="Première lettre: ")
select_first_letter = alt.selection_single(name="firstletter", fields=["first_letter"], bind=dropdown_letter, init={"first_letter": 'A'})

slider_docfreq = alt.binding_range(min=cfs['cfs'].min(), max=cfs['cfs'].max(), step=10, name="Nombre Minimum d'utilisations: ")
select_nb_appears = alt.selection_single(name="nbappears", fields=["cfs"], bind=slider_docfreq, init={"cfs": 101})

alt.Chart(cfs.sort_values('word')).mark_bar().encode(
    y=alt.Y(
        "cfs:Q", 
        title="Nombre d'utilisations du mot",
        scale=alt.Scale(domain=[0, cfs['cfs'].max()])
    ),
    x=alt.X(
        "word:O", 
        axis=alt.Axis(labelAngle=-45),
        title="Mot"
    ),
    color=alt.Color("cfs", scale=alt.Scale(scheme="redyellowgreen", domain=[cfs['cfs'].min(), cfs['cfs'].max()])),
    tooltip=[alt.Tooltip(field="word", title="Mot"), alt.Tooltip(field="cfs", title="# Utilisations")]
).add_selection(
    select_first_letter,
    select_nb_appears
).transform_filter(
    select_first_letter
).transform_filter(
    "datum.cfs >= nbappears_cfs"
).properties(
    height=400
)

alt.Chart(...)

In [9]:
# Les Titres de Blaah

In [10]:
# * Le modèle: "xxx-OM (score), La Canebière académie VERBE COD..."
# * Lyon-OM (2-1), La Canebière académie ne tient pas la distance

In [11]:
matchs = resultats(blaah)
notation = notes(blaah)



___


# Scores (Extraits du Titre)

### Nombre de buts dans les matches

In [12]:
matchs["Nb Buts"] = matchs["Buts_R"] + matchs["Buts_V"]

In [13]:
alt.Chart(matchs[["Nb Buts"]]).mark_bar().encode(
    x=alt.X("Nb Buts:O", axis=alt.Axis(labelAngle=0)),
    y="count():Q",
    color=alt.Color("Nb Buts:O", scale=alt.Scale(scheme="greens")),
    tooltip=["Nb Buts:O", alt.Tooltip("count():Q", title="Nb Matches")]
).properties(
    width=DEFAULT_WIDTH
)

alt.Chart(...)

### Nombre de buts de l'OM

In [14]:
alt.Chart(matchs[["Buts_OM"]]).mark_bar().encode(
    x=alt.X("Buts_OM:O", title="Buts de l'OM", axis=alt.Axis(labelAngle=0)),
    y="count():Q",
    color="Buts_OM:O",
    tooltip=[alt.Tooltip("Buts_OM:O", title="Buts de l'OM"), alt.Tooltip("count():Q", title="Nb Matches")]
).properties(
    width=DEFAULT_WIDTH
)

alt.Chart(...)

### Nombre de buts de l'adversaire

In [15]:
alt.Chart(matchs[["Buts_Adversaire"]]).mark_bar().encode(
    x=alt.X("Buts_Adversaire:O", title="Buts de l'adversaire", axis=alt.Axis(labelAngle=0)),
    y="count():Q",
    color=alt.Color("Buts_Adversaire:O", scale=alt.Scale(scheme="reds")),
    tooltip=[alt.Tooltip("Buts_Adversaire:O", title="Buts de l'OM"), alt.Tooltip("count():Q", title="Nb Matches")]
).properties(
    width=DEFAULT_WIDTH
)

alt.Chart(...)

### Différence de But par Adversaire

In [16]:
by_adv = matchs.groupby("Adversaire").size()

In [17]:
# Il va falloir traiter les doublons...

# * ASSE / Saint-Etienne / Saint-Étienne
# * TFC / Toulouse
# * MHSC / Montpellier
# * Gazélec / Gazéléc
# * Konyaspot / Konyasport
# * Salzbourg / Salzburg
# * Athletic / Bilbao

In [18]:
normalize = [
    {"dups": ["ASSE", "Saint-Etienne", "Saint-Étienne"], "norm": "Saint-Étienne"},
    {"dups": ["TFC", "Toulouse"], "norm": "Toulouse"},
    {"dups": ["MHSC", "Montpellier"], "norm": "Montpellier"},
    {"dups": ["Gazélec", "Gazéléc"], "norm": "Gazélec Ajaccio"},
    {"dups": ["Konyaspor", "Konyasport"], "norm": "Konyaspor"},
    {"dups": ["Salzbourg", "Salzburg"], "norm": "Salzburg"},
    {"dups": ["Athletic", "Bilbao"], "norm": "Athletic Bilbao"},
    {"dups": ["Atlético"], "norm": "Atletico Madrid"}
]

In [19]:
matchs["Publications"] = 1

In [20]:
for dedup in normalize:
    matchs.loc[matchs["Adversaire"].isin(dedup["dups"]), "Adversaire"] = dedup["norm"]

In [21]:
by_adv = matchs.groupby("Adversaire").agg({"Publications": "sum", "Buts_OM": "sum", "Buts_Adversaire": "sum"})
by_adv.reset_index(inplace=True)

In [22]:
by_adv["Différence de Buts"] = by_adv["Buts_OM"] - by_adv["Buts_Adversaire"]

In [23]:
slider = alt.binding_range(min=by_adv["Publications"].min(), max=by_adv["Publications"].max(), step=1, name="Nombre Minimum de Matchs: ")
select_nb_matches = alt.selection_single(name="matches", fields=["Publications"], bind=slider, init={"Publications": 1})

alt.Chart(by_adv).mark_bar().encode(
    y="Différence de Buts",
    x=alt.X(
        "Adversaire:O", 
        sort=alt.EncodingSortField(field="Différence de Buts", order="ascending"),
        axis=alt.Axis(labelAngle=-45)
    ),
    color=alt.Color("Différence de Buts", scale=alt.Scale(scheme="redyellowgreen")),
    tooltip=["Adversaire", "Différence de Buts", alt.Tooltip("Publications", title="Nb Matches")]
).add_selection(
    select_nb_matches
).transform_filter(
    "datum.Publications >= matches_Publications"
). properties(height=600,width=1200)

alt.Chart(...)

In [24]:
### Différentiel Victoire / Défaite par Adversaire

In [25]:
matchs["Victoire"] = matchs["Buts_OM"] > matchs["Buts_Adversaire"]
matchs["Défaite"] =  matchs["Buts_OM"] < matchs["Buts_Adversaire"]
matchs["Nul"] =  matchs["Buts_OM"] == matchs["Buts_Adversaire"]

In [26]:
by_adv = matchs.groupby("Adversaire").agg({"Publications": "sum", "Victoire": "sum", "Défaite": "sum", "Nul": "sum"})
by_adv.reset_index(inplace=True)
by_adv["Différence Victoire / Défaite"] = by_adv["Victoire"].astype(int) - by_adv["Défaite"].astype(int)

In [27]:
chart = alt.Chart(by_adv).mark_bar().encode(
    y="Différence Victoire / Défaite",
    x=alt.X(
        "Adversaire:O", 
        sort=alt.EncodingSortField(field="Différence Victoire / Défaite"),
        axis=alt.Axis(labelAngle=-45)
    ),
    color=alt.Color("Différence Victoire / Défaite", scale=alt.Scale(domain=[-10, 10], scheme="redyellowgreen")),
    tooltip=["Adversaire", "Victoire", "Nul", "Défaite", alt.Tooltip("Publications", title="Nb Matches")]
).add_selection(
    select_nb_matches
).transform_filter(
    "datum.Publications >= matches_Publications"
). properties(height=600,width=1200)

chart

alt.Chart(...)

# Les Verbes dans les Titres

In [28]:
titres = pd.DataFrame(blaah["Titre"].copy())
titres["Titre_Part2"] = titres["Titre"].str.lower().str.extract(r"^.+(la\s+canebière\s+académiq?u?e[\w\s]+)")

In [29]:
titres.dropna(subset=["Titre_Part2"], inplace=True)

In [30]:
titres["Titre_Part2"] = titres["Titre_Part2"].str.replace(r"la\s+canebière\s+académiq?u?e", "elle", regex=True)

In [31]:
fr = spacy.load('fr_core_news_sm')

In [32]:
titres["Titre_Part2_doc"] = titres["Titre_Part2"].apply(fr)

In [33]:
def extract_verb(x):
    v = [t.lemma_ for t in x if t.pos_ == "VERB"]
    if len(v) == 0:
        return np.nan
    return lemmatizer.lemmatize(v[0], "v")

titres["Verbe"] = titres["Titre_Part2_doc"].apply(extract_verb)
titres["Publications"] = 1

In [34]:
def group_verb(x: str) -> int:
    if x.endswith("er"):
        return 1

    if x.endswith("oir"):
        return 3

    if x.endswith("ir"):
        return 2

    return 3

verbes = pd.DataFrame(titres["Verbe"].dropna().unique(), columns=["Verbe"])
verbes["groupe"] = verbes["Verbe"].apply(group_verb)

In [35]:
chart = alt.Chart(titres[["Verbe", "Publications"]].dropna().sort_values(["Publications", "Verbe"], ascending=[False, True])).mark_bar().encode(
    x=alt.X(
        field="Verbe", 
        type="ordinal", 
        sort=alt.EncodingSortField(field="Occurences", order="descending"),
        axis=alt.Axis(labelAngle=-45, labelFontSize=14)
    ),
    y="Occurences:Q",
    color=alt.Color("Occurences:Q", scale=alt.Scale(scheme="greenblue")),
    tooltip=["Verbe", "Occurences:Q"]
).transform_aggregate(
    groupby=["Verbe"],
    Occurences="sum(Publications)"
).transform_filter(
    alt.datum.Occurences >= 1
)

chart.configure_header(
    titleColor='green',
    titleFontSize=14,
    labelColor='red',
    labelFontSize=14
)

chart

alt.Chart(...)



___


# Les Notes (Extraites du texte de l'académie)

In [36]:
stats = pd.DataFrame({"Académie": ["Académie", "Académie"], "Notes": ["Récupérées", "Non Récupérées"], "Nombre": [notation["Date"].nunique(), blaah.shape[0] - notation["Date"].nunique()]})

alt.Chart(stats).mark_bar().encode(
    x=alt.X("Académie:N", axis=alt.Axis(labels=False)),
    y=alt.Y("Nombre:Q", stack="zero"),
    color=alt.Color("Notes:N", legend=alt.Legend(title="Récupération Automatique"), scale=alt.Scale(domain=["Récupérées", "Non Récupérées"], range=["green", "red"])),
    tooltip="Nombre:Q"
)

alt.Chart(...)

In [37]:
by_joueur = notation.groupby("Joueur").agg({"Note_num": ["count", "mean"]})
by_joueur.columns = by_joueur.columns.droplevel()
by_joueur.reset_index(inplace=True)

In [38]:
chart = alt.Chart(by_joueur).mark_bar().encode(
    x=alt.X(
        field="Joueur", 
        type="ordinal", 
        sort=alt.EncodingSortField(field="count", order="descending"),
        axis=alt.Axis(labelAngle=-45, labelFontSize=14)
    ),
    y=alt.Y("count:Q", title="Nombre de Notes"),
    color=alt.Color("count:Q", scale=alt.Scale(scheme="greenblue")),
    tooltip=["Joueur", alt.Tooltip("count:Q", title="# Notes")]
)

chart.configure_header(
    titleColor='green',
    titleFontSize=14,
    labelColor='red',
    labelFontSize=14
)

chart

alt.Chart(...)

In [39]:
# nb_notes = notes["Joueur"].value_counts()

# alt.Chart(notes[notes["Joueur"].isin(nb_notes[nb_notes >= 10].index)][["Joueur", "Note_num"]]).transform_density(
#     'Note_num',
#     as_=['Note', 'density'],
#     extent=[0, 5],
#     groupby=['Joueur']
# ).mark_area(orient='horizontal').encode(
#     y='Note:Q',
#     color='Joueur:N',
#     x=alt.X(
#         'density:Q',
#         stack='center',
#         impute=None,
#         title=None,
#         axis=alt.Axis(labels=False, values=[0],grid=False, ticks=True),
#     ),
#     column=alt.Column(
#         'Joueur:N',
#         header=alt.Header(
#             titleOrient='bottom',
#             labelOrient='bottom',
#             labelPadding=0,
#             labelFontWeight="bold",
#             labelBaseline="bottom",
#             labelAngle=-45
#         ),
#     )
# ).properties(
#     width=50
# ).configure_facet(
#     spacing=0
# ).configure_view(
#     stroke=None
# )

# Toutes les Notes, Tous les Joueurs, Tous les Matches

In [40]:
by_joueur_by_note = notation.groupby(["Joueur", "Note_num"]).agg({"Date": "count"})
by_joueur_by_note = by_joueur_by_note.reset_index()
by_joueur_by_note.columns = ["Joueur", "Note", "count"]



In [41]:
slider = alt.binding_range(min=by_joueur["count"].min(), max=by_joueur["count"].max(), step=1, name="Nombre Minimum de Notes: ")
select_nb_matches = alt.selection_single(name="matches", fields=["count"], bind=slider, init={"count": 1})

classement_moyenne = alt.Chart(notation).mark_bar().transform_aggregate(
    count="count(Note_num)",
    moyenne="mean(Note_num)",
    groupby=["Joueur"]
).encode(
    x=alt.X(
        field="Joueur", 
        type="ordinal", 
        sort="-y",
        axis=alt.Axis(labelAngle=-45, labelFontSize=14)
    ),
    y=alt.Y("moyenne:Q", title="Moyenne"),
    color=alt.Color("moyenne:Q", scale=alt.Scale(scheme="redyellowgreen", domain=[0.0, 5.0])),
    tooltip=["Joueur", alt.Tooltip("count:Q", title="# Notes"), alt.Tooltip("moyenne:Q", title="Moyenne", format='.2f')]
).add_selection(
    select_nb_matches
).transform_filter(
    'datum.count >= matches_count'
)

classement_moyenne.configure_header(
    titleColor='green',
    titleFontSize=14,
    labelColor='red',
    labelFontSize=14
)

classement_moyenne


alt.Chart(...)

In [42]:
notes_joueurs = alt.Chart(notation).mark_bar().encode(
    y=alt.Y(
        'Joueur:N',
        title=None,
        axis=alt.Axis(labelFontSize=16),
    ),
    x=alt.X(
        'count(Note_num):Q', 
        title="",
        stack='normalize',
        axis=alt.Axis(labels=False, ticks=False)
    ),
    order=alt.Order("Note_num:Q", sort="ascending"),
    color=alt.Color('Note_num:Q', scale=alt.Scale(scheme="redyellowgreen", domain=[0.0, 5.0])),
    tooltip=["Joueur", alt.Tooltip("Note_num:Q", title="Note"), alt.Tooltip("count(Note_num):Q", title="Nombre de fois")]
)

moyennes = alt.Chart(notation).mark_bar().transform_aggregate(
    count="count(Note_num)",
    moyenne="mean(Note_num)",
    groupby=["Joueur"]
).encode(
    y=alt.Y(
        field="Joueur", 
        type="ordinal", 
        title="",
        axis=alt.Axis(labels=False, ticks=False)
    ),
    x=alt.X(
        "moyenne:Q", 
        title="Moyenne",
        axis=alt.Axis(grid=False)
    ),
    color=alt.Color("moyenne:Q", scale=alt.Scale(scheme="redyellowgreen", domain=[0.0, 5.0])),
    tooltip=["Joueur", alt.Tooltip("count:Q", title="# Notes"), alt.Tooltip("moyenne:Q", title="Moyenne", format='.2f')]
)

notes_joueurs | moyennes

alt.HConcatChart(...)

In [43]:
# alt.Chart(notes).mark_point(shape="square", size=2).encode(
#     x=alt.X(
#         "Match:O",
#         sort=alt.EncodingSortField("sort", order="descending"), 
#         axis=alt.Axis(labels=False, ticks=False)
#         ),
#     y=alt.Y(
#         "Joueur:N",
#         axis=alt.Axis(labels=False, ticks=False)
#         ),
#     color=alt.Color("Note_num:Q", scale=alt.Scale(scheme="redyellowgreen")),
#     #size=alt.Size("count:Q", ),
#     tooltip=["Joueur", alt.Tooltip("Note_num:Q", title="Note"), "Adversaire", "Date"]
# ).properties(
#     height=400,
#     width=1200
# )

In [44]:
# width = 1200
# nb_matches = notes["Match"].nunique()
# nb_joueurs = notes["Joueur"].nunique()

# select_joueurs = alt.selection_multi(fields=["Joueur"])

# joueurs = alt.Chart(pd.DataFrame({"Joueur": notes["Joueur"].unique()})).mark_rect().encode(
#     x=alt.X(
#         "Joueur:N",
#         axis=alt.Axis(labelAngle=-45),
#     ),
#     color=alt.condition(select_joueurs, alt.Color('Joueur:N', legend=None), alt.value('lightgray'))
# ).add_selection(
#     select_joueurs
# ).properties(
#     width=width
# )

# heatmap = alt.Chart(notes).mark_point(shape="square", size=2).encode(
#     x=alt.X(
#         "Match:O",
#         sort=alt.EncodingSortField("sort", order="descending"), 
#         axis=alt.Axis(labels=False, ticks=False)
#         ),
#     y=alt.Y(
#         "Joueur:N",
#         axis=alt.Axis(labels=False, ticks=False)
#         ),
#     color=alt.Color("Note_num:Q", scale=alt.Scale(scheme="redyellowgreen")),
#     #size=alt.Size("count:Q", ),
#     tooltip=["Joueur", alt.Tooltip("Note_num", title="Note"), "Adversaire", "Date"]
# ).properties(
#     height=400,
#     width=width
# ).transform_filter(
#     select_joueurs
# )

# joueurs & heatmap

# Les notes de l'OM par match

In [45]:
by_match_by_note = notation.groupby(["Match", "Note_num"]).agg({"Joueur": "count", "sort": "max"}).reset_index()


In [46]:
circles = alt.Chart(by_match_by_note).mark_circle().encode(
    y=alt.Y(
        'Match:N',
        title=None,
        axis=alt.Axis(ticks=False, grid=False, labelPadding=20, labelFontSize=14),
        sort=alt.EncodingSortField("sort", op="max", order="descending")
    ),
    x=alt.X(
        'Note_num:Q',
        title='Note',
        axis=alt.Axis(grid=False)
    ),
    color=alt.Color(
        'Note_num:Q', 
        legend=None, 
        scale=alt.Scale(domain=[0.0,5.0], scheme="redyellowgreen")
    ),
    size=alt.Size(
        "Joueur:Q",
        legend=None,
        scale=alt.Scale(domain=[0.0, by_match_by_note["Joueur"].max()], range=[0.0, 2000.0])
    ),
    tooltip=["Match:N", alt.Tooltip("Note_num:Q", title="Note"), alt.Tooltip("Joueur:N", title="# Joueurs")]
)

bars = alt.Chart(by_match_by_note).mark_bar().encode(
    y=alt.Y(
        'Match:N',
        title=None,
        axis=alt.Axis(ticks=False, grid=False, labelPadding=20, labels=False),
        sort=alt.EncodingSortField("sort", op="max", order="descending")
    ),
    x=alt.X(
        'Note_num:Q',
        stack="normalize",
        axis=alt.Axis(grid=False)
    ),
    color=alt.Color(
        'Note_num:Q', 
        legend=None, 
        scale=alt.Scale(domain=[0.0, 5.0], scheme="redyellowgreen")
    ),
    tooltip=["Match:N", alt.Tooltip("Note_num:Q", title="Note"), alt.Tooltip("Joueur:N", title="# Joueurs")]
)

boxplots = alt.Chart(notation[["Match", "sort", "Note_num"]].rename(columns={"Note_num": "Note"}).sort_values("sort", ascending=False)).mark_boxplot(extent="min-max").encode(
    y=alt.Y(
        'Match:N',
        title=None,
        axis=alt.Axis(ticks=False, grid=False, labels=False),
        sort=alt.EncodingSortField(order=None)
    ),
    x=alt.X(
        'Note:Q',
        axis=alt.Axis(grid=False,)
    ),
    color=alt.Color("mean(Note):Q", scale=alt.Scale(domain=[0.0, 5.0], scheme="redyellowgreen")),
    tooltip=["Match:N"]
)


circles | bars | boxplots

alt.HConcatChart(...)

# La Canebière Académie, des origines à aujourd'hui

## Publications par auteur

In [47]:
df = df.reset_index()

In [48]:
alt.Chart(df[["Auteur", "Publications"]]).mark_bar().encode(
    x=alt.X(
        "Auteur:N",
        axis=alt.Axis(labelAngle=0)
    ),
    y=alt.Y(
        "count(Publications):Q",
        axis=alt.Axis(title="Académies")
    ),
    color="Auteur:N",
    tooltip=["Auteur", alt.Tooltip("count(Publications):Q", title="Académies")]
).properties(
    width=DEFAULT_WIDTH
)

alt.Chart(...)

In [49]:
alt.Chart(df[["Auteur", "Publications"]]).mark_arc(innerRadius=50, outerRadius=300).encode(
    theta=alt.Theta(
        "count(Publications):Q",
        title="Académies"
    ),
    color="Auteur:N",
    tooltip=["Auteur", alt.Tooltip("count(Publications):Q", title="Académies")]
).properties(
    width=DEFAULT_WIDTH
)

alt.Chart(...)

## Publications par Année et Auteur

In [50]:
raw_counts = alt.Chart(df[["Date", "Auteur", "Publications"]]).mark_bar().encode(
    x=alt.X("year(Date):O", title=None, axis=alt.Axis(ticks=False, labels=False)),
    y=alt.Y("count():Q", title="Académies"),
    color="Auteur:N",
    tooltip=[alt.Tooltip("year(Date)", title="Année"), "Auteur", alt.Tooltip("count()", title="Académies")]
).properties(
    width=DEFAULT_WIDTH
)

pct_counts = alt.Chart(df[["Date", "Auteur", "Publications"]]).mark_bar().encode(
    x=alt.X("year(Date):O", title="Année", axis=alt.Axis(ticks=False)),
    y=alt.Y("count():Q", title="Académies", stack="normalize", axis=alt.Axis(format="%")),
    color="Auteur:N",
    tooltip=[alt.Tooltip("year(Date)", title="Année"), "Auteur", alt.Tooltip("count()", title="Académies")]
).properties(
    width=DEFAULT_WIDTH
)

raw_counts & pct_counts

alt.VConcatChart(...)

## Longueur du texte par auteur

In [51]:
alt.Chart(df[["Auteur", "nb_tokens"]]).transform_density(
    'nb_tokens',
    as_=['Nombre de Mots', 'density'],
    extent=[0, 6000],
    groupby=['Auteur']
).mark_area(orient='horizontal').encode(
    y='Nombre de Mots:Q',
    color='Auteur:N',
    x=alt.X(
        'density:Q',
        stack='center',
        impute=None,
        title=None,
        axis=alt.Axis(labels=False, values=[0],grid=False, ticks=True),
    ),
    column=alt.Column(
        'Auteur:N',
        header=alt.Header(
            titleOrient='bottom',
            labelOrient='bottom',
            labelPadding=0,
            labelFontWeight="bold",
            labelBaseline="bottom"
        ),
    )
).properties(
    width=200
).configure_facet(
    spacing=0
).configure_view(
    stroke=None
)

alt.Chart(...)